# RDBMS - MySQL 

## 00 - Introduction

Among the Relational DBMSs, the most widely known are Oracle, SQLite, Postgress, MariaDB, MySQL.

Each one of them is characterized by a different set of "variations" on top of the base SQL language, although usually minor.

We will use **MySQL** to run exercises about Relational DB transactions using the SQL language, as it is *today* at the top of the list of most widely used RDBs. 

https://db-engines.com/en/ranking_trend/relational+dbms

https://www.statista.com/statistics/809750/worldwide-popularity-ranking-database-management-systems/

https://insights.stackoverflow.com/survey/2021#most-popular-technologies-database

MySQL programming interfaces exist for many languages, including C, C++, Go, Java, Perl, PHP, Python, etc...

Even simply referring to Python, we can count on several options to connect and interact with the DBs. 

Let's explore a couple of them...

## 01 - Create a connection to MySQL 

A MySQL server is in execution on one of your Docker containers.

We can access it via the MySQL server credential we have defined in the docker-compose yml.

A `root` user is created by default with:
- user: `root`
- password: `root_pwd`

A non-`root` user is also created by default with:
- user: `my_user`
- password: `my_pwd`

#### Interactive 

We can interact with the MySQL server by logging in interactively to its docker container.

Check the `CONTAINER ID` of the container named `mysql_db` via:
    
```bash 
$ docker ps 
```

And run `bash` (or `/bin/bash`) in interactive mode attaching it to the terminal (`-it`) on the container:

```bash
$ docker exec -it <YOUR CONTAINER ID> bash
```

From inside the container we can use the RDBMS interface as if we were logged into a remote MySQL server hosting our DBs

```bash
$ mysql -u <EITHER ROOT OR USER> -p
``` 

We can then inspect the MySQL server to show us all DBs:
    
```mysql
SHOW DATABASES;
```

_NB_: remember to end a SQL command with a semicolon `;`

#### mysql.connector

A more pythonic way of communicating with a MySQL server is by using a dedicated driver.

We will use `mysql.connector`, which has already been installed in the Jupyter-notebook container for you.

The connector offers an interface to declare a connection object to the server, and provides a series of functionalities to issue transactions and fetch records from DBs.

We start by declaring a connection to our MySQL server.

_NB_: the server is hosted in a different container from the notebook... we are simulating a connection between two differen machines, a client and a server.

In [ ]:
# import the connector
import mysql.connector

# declare a connection to the MySQL server 
# the hostname (or IP) of the server machine should be passed
db = mysql.connector.connect(
  user="root",
  password="root_pwd",
  host="db", # in this case 'db' is the equivalent of the IP address of the server 
             # or 'localhost' if running mysql locally
)

print(db)

At this point a DB connection is enstablished

To interact with the DB via python and mysql.connector we need a "handle", known as a cursor, which has to be instantiated.

Using this connector to interact with the DB, all SQL statements are executed using the cursor.

In [ ]:
# create our db cursor object
dbc = db.cursor()

The cursor allows to execute all SQL transactions on the DB as if we were logged into the server.

If a transaction will fetch a result from the DB (a set of records are returned), the connector object will retain the results.

This might come in handy for us to use it in a more "pythonic" way later on, interfacing our DB query with other Python statements.

The syntax for issuing a generic SQL statement is the following:

```python
connector_object.execute(my_sql_query)
```

For instance, let's try to execute the same check as before, by asking MySQL to show us all available DBs...

In [ ]:
# show all available databases
dbc.execute(
"SHOW DATABASES"
)

No output is printed as the result of this SQL transaction is in fact "collected" into the cursor as a list of records (tuples).

We can simply loop over them to return the results.

In [ ]:
# loop over the container to fetch the results
for _ in dbc:
    print(_)

If we are `root` users in this example, we are able to see inner structure of the mysql server, which already contains a few dbs by default. 

Once fetched the output of the transaction, the cursor reaches "the end" of the records, and is available to perform a new transaction

In [ ]:
# use fetch to retrieve one, many, or all entries in the cursor
dbc.fetchone()

# dbc.fetchmany(2)

# dbc.fetchall()

In the case one wants to perform a new transaction without collecting the output of the previos one from the cursor, a reset have to be issued first:

```python 
connector_object.reset()
```


In the case a generic user is instead logged into the db (i.e. non the `root` user), it will not have access to a set of functionalities, and will not be able to see the previous list of all databases.

Some of those are in fact protected and used to store additional information on the state of the MySQL server, the users connected, ...

In [ ]:
udb = mysql.connector.connect(
  user="my_user",
  password="my_pwd",
  host="db",
)

udbc = udb.cursor()

udbc.execute(
"SHOW DATABASES"
)

udbc.fetchall()

#### iPython magic

An alternative way to perform queries from Python over a Jupyter-notebook is by using some notebook "magic", based on iPython and SQLAlchemy.

This is a similar thing to what is usually done to load inline a figure from matplotlib (the `%matplotlib inline` thingy).

To instruct iPython to interpret SQL commands, and to connect to the proper DB we have to: 
1. load the extension for SQL language
2. set the environment variable to point to the connection to the DB

In [1]:
%load_ext sql

%env DATABASE_URL=mysql+mysqlconnector://root:root_pwd@db

env: DATABASE_URL=mysql+mysqlconnector://root:root_pwd@db


Now, the notebooks cells can perform SQL transactions directly in plain SQL, by starting the cell with `%%sql`.

By default, the result is also printed with the `pretty` pandas-like format.

In [2]:
%%sql

SHOW DATABASES;

5 rows affected.


[('IMDb',),
 ('information_schema',),
 ('mysql',),
 ('performance_schema',),
 ('sys',)]

An additional benefit is that a single `%slq` (not a double `%%sql`) can be used to join a SQL query with any Python command

In [ ]:
my_python_var = %sql SHOW DATABASES

print(my_python_var)

The combination of either of the two pythonic methods can be used to easily redirect the output of DB transactions to exploit all other well-known python modules, e.g. plotting with matplotlib

In [ ]:
import matplotlib.pyplot as plt
%matplotlib inline

plt.hist(my_python_var);
plt.xticks(rotation='vertical');

## 02 Database and Table creation

We have already seen how we inspect the server to see which DBs are present via the command:

```mysql
SHOW DATABASES;
```

We can start interacting with a specific DB by selecting which one to use via 

```mysql
USE <DB_NAME>;
```

If instead we want to create a new DB to work with, we can use the command

```mysql
CREATE DATABASE <DB_NAME>;
```

A more complex sintax can be used to create a new DB if and only if no other DB with the same name already exists.

```mysql
CREATE DATABASE IF NOT EXISTS <DB_NAME>;
```

If the user has been granted the right to access this DB, it's possible to start investigating the content of the DB in use.

Check if a DB named `my_db` exist, and if not, create one. 
Then, switch to the new DB to start using it.

In [ ]:
%%sql

CREATE DATABASE IF NOT EXISTS my_db;

In [ ]:
%%sql

SHOW DATABASES;

In [ ]:
%%sql

USE my_db;

All tables contained in the DB are shown in a similar way to what used to show all DBs on the server:

```mysql
SHOW TABLES;
```

_NB_: we are inspecting the content of a specific DB (the one selected with `USE <DB_NAME>`)

In [ ]:
%%sql 

SHOW TABLES;

The analogous pythonic way to execute the same list of commands (using the mysql.connector driver) is the following.

_NB_: This time, as we are not retrieving results from the server but we are instead creating a DB, we have to specify that we want to _commit_ a change to the server; 

In [ ]:
# defining the sql command line
sql_ = "CREATE DATABASE IF NOT EXISTS my_db;"

# instructing the cursor to execute it
dbc.execute(sql_)

# in this case the result of the sql transaction is not to return a list of items 
# it is instead a change in the DB structure
# therefore, for the change to have effect, a the change is to be committed to the DB
db.commit() 

All other commands, `USE` and `SHOW`, do not require any change to be committed, therefore we can simply issue them via the cursor.

In [ ]:
dbc.execute("USE my_db")

dbc.execute("SHOW TABLES")
dbc.fetchall()

So far the DB is empty, so let's use the same lines presented in the slides to create a dummy `Users` table.

Any table can then be inspected to check its schema by listing all attributes.

1. Create the `Users` table declaring the schema by defining each attributes
2. Check if the table has been created on the DB via a `SHOW` command
3. Check the Table schema by issuing `DESCRIBE <TABLE_NAME>`

In [ ]:
%%sql

CREATE TABLE Users (
    UserID varchar(30),
    BadgeNum int(16),
    FirstName varchar(255),
    LastName varchar(255),
    Age int,
    OtherAttr float
);

In [ ]:
%%sql 

SHOW TABLES;

In [ ]:
%%sql

DESCRIBE Users;

Following on the lines of the previous examples, perform the same transactions with the `mysql.connector` driver.

This time, as the `Users` table already exists, we can create a `Users_py` table.

Remember:
- Use the DB Cursor to execute the transactions
- Transaction that change the content of the DB have to be _committed_ to the DB
- Transactions returing the content of the DB host their results _in the cursor_

In [ ]:
dbc.reset() #che cosa fa?

In [ ]:
# create table
sql_ = "CREATE TABLE Users_py (\
    UserID varchar(30),\
    BadgeNum int(16),\
    FirstName varchar(255),\
    LastName varchar(255),\
    Age int,\
    OtherAttr float\
);"

dbc.execute(sql_)

db.commit()

In [ ]:
dbc.execute("SHOW TABLES")

In [ ]:
dbc.fetchall()

In [ ]:
# describe table
dbc.execute("DESCRIBE Users_py")

In [ ]:
dbc.fetchall()

## 03 Declaring contstraints and altering tables

Let's clean up all existing tables in our database.

To remove an existing table from a DB we can issue the instruction:
    
```mysql
DROP TABLE IF EXISTS <NAME OF YOUR TABLE>;
```

Be ***extremely careful*** when doing this... Dropping a Table means losing all records from that table, and severing all connections with other tables based on foreign keys. The entire DB might become unusable!


In [ ]:
%%sql 

DROP TABLE IF EXISTS Users;

Let's also drop the `Users_py` table using the Python connetor

In [ ]:
dbc.execute("DROP TABLE IF EXISTS Users_py")
db.commit()

Create a new `products` table with the following schema:

| Attribute | Type | Extra info | Constraint | 
| --- | --- | --- |--- |
| productID   | Integer | | NOT NULL AUTO_INCREMENT |
| productName | String | Max length 30 | DEFAULT "" |
| unitPrice   | Float | | NOT NULL DEFAULT 99999.99|
| unitsInStock | Integer | Unsigned | NOT NULL DEFAULT 0 |

`productID` will also be our `PRIMARY KEY`

This can be declared either inline or at the end of the table definition:

```mysql
productID INT NOT NULL UNIQUE AUTO_INCREMENT PRIMARY KEY
```

or 

```mysql
productID INT NOT NULL UNIQUE AUTO_INCREMENT
...
PRIMARY KEY (productID)
```

In [ ]:
%%sql

CREATE TABLE IF NOT EXISTS products (
         productID    INT          NOT NULL UNIQUE AUTO_INCREMENT PRIMARY KEY,
         productName  VARCHAR(30)  DEFAULT "" ,
         unitPrice    FLOAT        NOT NULL DEFAULT 99999.99,
         unitsInStock INT UNSIGNED NOT NULL DEFAULT 0
);

In [ ]:
%%sql

DESCRIBE products;

The table does not contain any constraint, default values, or keys.

A table can be altered by adding/removing Attributes, as well as by adding constraints.

Let's first add a new attribute to the table:

| Attribute | Type | Extra info | Constraint | 
| --- | --- | --- |--- |
| productID   | Integer | | NOT NULL AUTO_INCREMENT |
| productName | String | Max length 30 | DEFAULT "" |
| unitPrice   | Float | | NOT NULL DEFAULT 99999.99|
| unitsInStock | Integer | Unsigned | NOT NULL DEFAULT 0 |
| **isDiscontinued**  | **Bool** | | NOT NULL |

To alter a table and create a new column we can act on it with:

```mysql
ALTER TABLE <THE TABLE>
ADD COLUMN <NEW COL> <THE NEW ATTRIBUTE DECLARATION>;
```


Alter the `products` table and add the `isDiscontinued` attribute

In [ ]:
%%sql

ALTER TABLE products
ADD COLUMN isDiscontinued BOOL NOT NULL;

In [ ]:
%%sql 

DESCRIBE products;

`isDiscontinued` does however not contain any meaningful constraint or default value.
Let's consider `0` as a good default value:

| Attribute | Type | Extra info | Constraint | 
| --- | --- | --- |--- |
| productID   | Integer | | NOT NULL AUTO_INCREMENT |
| productName | String | Max length 30 | DEFAULT "" |
| unitPrice   | Float | | NOT NULL DEFAULT 99999.99|
| unitsInStock | Integer | Unsigned | NOT NULL DEFAULT 0 |
| isDiscontinued  | Bool | | NOT NULL **DEFAULT 0** |


We can use the same `ALTER TABLE` instruction to do this:
    
```mysql
ALTER TABLE <THE TABLE>
ALTER <ATTRIBUTE> SET DEFAULT <NEW DEFAULT>;
```

In [ ]:
%%sql

ALTER TABLE products
ALTER isDiscontinued SET DEFAULT 0;

In [ ]:
%%sql 

DESCRIBE products;

We can also impose `productName` to be not-null altering the table one final time.

| Attribute | Type | Extra info | Constraint | 
| --- | --- | --- |--- |
| productID   | Integer | | NOT NULL AUTO_INCREMENT |
| productName | String | Max length 30 | **NOT NULL** DEFAULT "" |
| unitPrice   | Float | | NOT NULL DEFAULT 99999.99|
| unitsInStock | Integer | Unsigned | NOT NULL DEFAULT 0 |
| isDiscontinued  | Bool | | NOT NULL DEFAULT 0 |


In MySQL, this implies to modify the entire attribute, thus the Type will have to be re-stated:
    
```mysql
ALTER TABLE <THE TABLE>
MODIFY <ATTRIBUTE> <ATTRIBUTE TYPE> <CONSTRAINT>;
```

In [ ]:
%%sql

ALTER TABLE products
MODIFY productName VARCHAR(30) NOT NULL DEFAULT "";

In [ ]:
%%sql

DESCRIBE products;

Let's now create a `suppliers` table with the following description:

| Attribute | Type | Extra info | Constraint | 
| --- | --- | --- |--- |
| supplierID   | Integer | | NOT NULL AUTO_INCREMENT |
| supplierName | String | Max length 30 | NOT NULL DEFAULT "" |
| countryCode   | Char | Length 3 | NOT NULL |
| email   | String | Max length 30  | NOT NULL |

`supplierID` is going to act as the table's primary key in this case.

In [ ]:
%%sql

CREATE TABLE suppliers (
    supplierID      INT NOT NULL UNIQUE AUTO_INCREMENT PRIMARY KEY,
    supplierName    VARCHAR(30) NOT NULL DEFAULT "",
    countryCode     CHAR(3) NOT NULL,
    email           VARCHAR(30) NOT NULL
);


In [ ]:
%%sql

DESCRIBE suppliers;

Alter the table to include a default "ITA" for `countryCode`

In [ ]:
%%sql 

ALTER TABLE suppliers 
ALTER countryCode SET DEFAULT "ITA";

In [ ]:
%%sql

DESCRIBE suppliers;

In [ ]:
%%sql

SHOW TABLES;

To enstablish a relation between the `products` and `suppliers` tables, we have to consider that:
    
- a supplier can supply multiple products
- a product can be supplied by multiple suppliers

This is a many-to-many relationship, which requires a supporting external table.

Create a new `supplier_to_product` table with the following attributes:
    
| Attribute | Type | Extra info | Constraint | 
| --- | --- | --- |--- |
| prodID   | Integer | | NOT NULL |
| supID    | Integer | | NOT NULL |


In [ ]:
%%sql 

CREATE TABLE supplier_to_product(
    prodID INT NOT NULL,
    supID  INT NOT NULL
);

In [ ]:
%%sql 

DESCRIBE supplier_to_product;

Neither prodID nor supID is a good primary key in this case, as we can have both appearing multiple times in the table.

However, a good primary key for this table is the combination (prodID,supID) which is absolutely unique, and thus, a good key.

We can alter the table to add the primary key statement:
    
```mysql
ALTER TABLE <TABLE>
ADD PRIMARY KEY <ATTRIBUTE COMBINATION>;
```

In [ ]:
%%sql

ALTER TABLE supplier_to_product
ADD PRIMARY KEY (prodID,supID);

In [ ]:
%%sql
ALTER TABLE supplier_to_product
DROP PRIMARY KEY;

In [ ]:
%%sql

DESCRIBE supplier_to_product;

Finally, we can link the 3 tables together by stating which attributes act as the foreign keys in the `supplier_to_product` table, and to which Attributes in the parent tables they refer to.

- `prodID` points to the `productID` attribute of `products` table
- `supID` points to the `supplierID` attribute of `supplier` table

```mysql
ALTER TABLE <TABLE>
ADD FOREIGN KEY (<ATTRIBUTE IN THIS TABLE>) REFERENCES <OTHER TABLE>(<ATTRIBUTE IN OTHER TABLE>);
```

In [ ]:
%%sql 

ALTER TABLE supplier_to_product 
ADD CONSTRAINT FK_prod
FOREIGN KEY (prodID) REFERENCES products(productID);

In [ ]:
%%sql 

ALTER TABLE supplier_to_product 
ADD CONSTRAINT FK_sup
FOREIGN KEY (supID) REFERENCES suppliers(supplierID);

In [ ]:
%%sql

DESCRIBE supplier_to_product;

## 04 Inserting Updating and Deleting records

The tables are currently empty. 
We can inspect the content of the tables by performing a simple query.

```mysql
SELECT * FROM <TABLE>;
```

To insert a single record into a table we can proceed in either of the two following ways:

1. By explicitly specifying the names of the columns when passing the tuple containing the values
```mysql
INSERT INTO <TABLE> (<COLUMN1>, <COLUMN2>, <COLUMN3>, ...)
VALUES (<VALUE1>, <VALUE2>, <VALUE3>, ...);
```
This will work also in the case attributes with a default value will not be explicitely passed


2. By implicitly using all the columns when passing the tuple containing the values
```mysql
INSERT INTO <TABLE> 
VALUES (<VALUE1>, <VALUE2>, ..., <VALUEn>);
```


_NB_: 1. is the usually recommended way to perform a data insertion in SQL.

Using the `mysql.connector` we can formulate the insert in a more pythonic way, e.g. to include this statement programmatically into a loop or a function call:
    
```python
sql_ = "INSERT INTO <TABLE> (<COLUMN1>, <COLUMN2>, <COLUMN3>, ...) VALUES (%s, %s, %s, ...)"
val_ = (<VALUE1>, <VALUE2>, <VALUE3>, ...)
db_cursor.execute(sql_, val_)
db.commit()
```

Being an active change to the DB istance (the data contained in the DB itself), remember to commit the insert.

- Verify that the product table is actually empty
- Isert the following list of products in the `products` table
- Check the content of the table after the transaction, to verify that both the AUTO_INCREMENT key and the default values have taken into account


| productName | unitPrice | unitsInStock | isDiscontinued | 
| --- | --- | --- |--- |
| "Founders Porter" | 4.9 | 12 | 0 |


In [ ]:
%%sql

SELECT * FROM products;

In [ ]:
%%sql

INSERT INTO products (productName, unitPrice, unitsInStock, isDiscontinued)
VALUES ("Founders Porter", 4.9, 12, 0);

In [ ]:
%%sql

SELECT * FROM products;

In [ ]:
%%sql

SELECT * FROM supplier_to_product;

Multi-values insert can be performed in a completely similar way, by separating multiple tuples by a comma:
    
```mysql
INSERT INTO <TABLE> (<COLUMN1>, <COLUMN2>, <COLUMN3>, ...)
VALUES 
(<VALUE11>, <VALUE12>, <VALUE13>, ...), 
(<VALUE21>, <VALUE22>, <VALUE23>, ...), 
(<VALUE31>, <VALUE32>, <VALUE33>, ...), 

```

The python-based command is similar to the previous one, but is drop the `execute` in favor of `executemany`, using as value a list of tuples

```python
sql_ = "INSERT INTO <TABLE> (<COLUMN1>, <COLUMN2>, <COLUMN3>, ...) VALUES (%s, %s, %s, ...)"
val_ = [
    (<VALUE11>, <VALUE12>, <VALUE13>, ...),
    (<VALUE21>, <VALUE22>, <VALUE23>, ...),
    (<VALUE31>, <VALUE32>, <VALUE33>, ...) ]
db_cursor.executemany(sql_, val_)
db.commit()
```


Add a few more products to the `product` table:
    
| productName | unitPrice | unitsInStock | isDiscontinued | 
| --- | --- | --- |--- |
| "Punk IPA" | 5.2 | 45 |  |
| "HB Dunkel" | 4.5 | 250 |  |
| "Forst Xmas " | 8.0 | 2 |  |
| "Damm Complot " | 3.7 | 120 |  |
     

In [ ]:
%%sql

INSERT INTO products (productName, unitPrice, unitsInStock)
VALUES     ('Punk IPA',     5.2,  45),
    ('HB Dunkel',    4.5, 250),
    ('Forst Xmas',   8.0,   2),
    ('Damm Complot', 3.7, 120);


In [ ]:
%%sql 

SELECT * FROM products;

Updating entries is a more delicate issue, as in a DB we can in principle modify all records associated with a number of conditions.
This makes the update operation quite powerful and possibly very error prone if not performed with extreme caution.

```mysql
UPDATE <TABLE>
SET <ATTRIBUTE> = <NEW VALUE>
WHERE <CONDITION>;
```

or

```python
sql_ = "UPDATE <TABLE> SET <ATTRIBUTE> = <NEW VALUE> WHERE <CONDITION>"
db_cursor.execute(sql)
db.commit()

```

Let's update a single record with a "very explicit" condition statement:

- Assign `isDiscontinued` equal to 1 to the "Forst Xmas" product
- Check if the update has taken place

In [ ]:
%%sql

UPDATE products
SET isDiscontinued = 1
WHERE (productName = "Forst Xmas");

In [ ]:
%%sql

SELECT * FROM products;

Similarly, deleting entries is quite a risky task if not done with plenty of caution, as a wrong `WHERE` condition might inadvertly lead to the deletion of a large part of your DB records. 

Remember, with `DELETE` we do remove entire records (i.e. tuples) from the DB, not just the content of the `WHERE` conditional statement. 

```mysql
DELETE FROM <TABLE>
WHERE <CONDITION>;
```

or

```python
sql_ = "DELETE FROM <TABLE> WHERE <CONDITION>"
db_cursor.execute(sql)
db.commit()

```

- Delete all products whose name begins with 'F' and ends with 's'
- Check if the update has taken place

In [ ]:
%%sql

DELETE FROM products
WHERE (productName LIKE 'F%s');

In [ ]:
%%sql

SELECT * FROM products;

- Populate the `suppliers` table according to the following list


| supplierName | countryCode | email|
| --- | --- | ---|
| "A hop in the park" | "USA" | "contactme@ahop.com" |
| "Allez Hops! Cave à bièr" | "FRA" | "itsme@allezhops.com" |
| "Wild Hops " | "ITA" | "myemail@wildhops.it" |
|"Beer Paradise"|"ITA"|"beer@beerparadise.it"|


In [ ]:
%%sql

INSERT INTO suppliers (supplierName, countryCode, email) 
VALUES
("A hop in the park","USA","contactme@ahop.com"),
("Allez Hops! Cave à bièr","FRA","itsme@allezhops.com"),
("Wild Hops","ITA","myemail@wildhops.it"),
("Beer Paradise","ITA","beer@beerparadise.it");

In [ ]:
%%sql

SELECT * FROM suppliers;

Complete the DB with the two additional steps:

- Update the "A hop in the park" email address to "anewemail@ahop.com"
- Populate the table of connections between products and suppliers
    - Remember that the `supplier_to_product` table is linked to the other two via the respective Foreign Keys 

| supplier | products provided |
| --- | --- | 
| "A hop in the park" | "Punk IPA", "HB Dunkel" |

In [ ]:
sql_ = "UPDATE suppliers SET email = %s WHERE supplierName LIKE %s;"
val_ = ('anewemail@ahop.com', 'A hop%')
dbc.execute(sql_, val_)
db.commit()
     
dbc.execute("SELECT * FROM suppliers"); 
dbc.fetchall()

In [ ]:
%%sql 

SELECT * FROM products;

In [ ]:
%%sql 

SELECT * FROM suppliers;

In [ ]:
%%sql

DESCRIBE supplier_to_product;

In [ ]:
%%sql

INSERT INTO supplier_to_product (supID, prodID)
VALUES (1, 2),
       (1, 3);

In [ ]:
%%sql 

SELECT * FROM supplier_to_product;

Export the DB you have created into a .sql file, and store it for later use.

1. connect to the "server" docker container using bash
2. dump the DB via the command:
    
```bash
$ mysqldump -u <USER> -p <DB NAME>  >  <FULL/PATH/TO/NEW/DB_DUMP.sql>
```

3. use the folder `/mapd-workspace/dbs` to store the file, as it's the one currently visible from both in- and out-side the container

```bash
mysqldump -u root -p my_db > /mapd-workspace/dbs/DB_DUMP.sql
```

## 04 Basic queries 

### EDIT (same info in Section 05) ###

If you have saved your DB locally into a `.sql` file, you can restore it by loading it into the server.

1. Create a new DB named `my_db`
```
CREATE DATABASE IF NOT EXISTS my_db;
```
2. Login in interactive mode into the MySQL server 
```bash 
$ docker exec -it mysql_db_1 bash
```
2. Import the content of the `.sql` file (e.g. `/mapd-workspace/dbs/my_db.sql`) into the newly created DB
    
```bash
$ mysql -u root -p my_db < /mapd-workspace/dbs/DB_DUMP.sql
```


In [ ]:
%load_ext sql

%env DATABASE_URL=mysql+mysqlconnector://root:root_pwd@db

In [ ]:
%%sql

USE my_db;

In [ ]:
%%sql
SHOW TABLES;

- Get the email of all suppliers from Italy

In [ ]:
%%sql

SHOW TABLES;

In [ ]:
%%sql

DESCRIBE suppliers;

In [ ]:
%%sql

SELECT * FROM suppliers;

In [ ]:
%%sql

SELECT email
FROM suppliers
WHERE (countryCode = "ITA");

- Get all information for products with unit price greater than 4

In [ ]:
%%sql

DESCRIBE products;

In [ ]:
%%sql

SELECT * FROM products;

In [ ]:
%%sql

SELECT *
FROM products
WHERE (unitPrice > 4);

- Select all products with unit cost less than 5 and list them in descending order of units in stock

In [ ]:
%%sql

SELECT *
FROM products
WHERE (unitPrice<5)
ORDER BY unitsInStock DESC;

**Group by** is a common statement which allows to perform data aggregation.

If familiar with `pandas`, this should not come any new to you.

Just remember:
1. No group by statement is possible without an aggregation function.
2. Group by are quite computationally expensive. In case of large databases group by operations might require a long time to execute

- plot the distribution of suppliers by country

In [ ]:
%%sql
SELECT countryCode, COUNT(2) AS Number FROM suppliers 
GROUP BY countrycode;

In [ ]:
df = %sql SELECT countryCode, COUNT(2) AS Number FROM suppliers GROUP BY countrycode;

In [ ]:
type(df)

In [ ]:
import matplotlib.pyplot as plt
import numpy as np
import pandas as pd

df_pandas=pd.DataFrame(df)
plt.bar(df_pandas["countryCode"],df_pandas["Number"])

In [ ]:
%%sql

SELECT  countryCode, COUNT(countryCode) AS nSupp
FROM suppliers
GROUP BY countryCode;

In [ ]:
res_ = %sql SELECT COUNT(countryCode) AS count, countryCode FROM suppliers GROUP BY countryCode;

print (res_);

In [ ]:
res_.bar();

The main strength of Relational DBs is the possibility of matching information from different tables though **Join** operations.

A join, either performed explicitely or implicitely is:

Just remember:
1. Computationally expensive. In case of large databases group by operations might require a long time to execute
2. Very easy to be done wrong, thus resulting in non-meaningful results

Be sure on which attributes (most often keys) you are performing a join operation.

- Join the `supplier_to_product` table with the `suppliers` table 

In [ ]:
%%sql

DESCRIBE suppliers;

In [ ]:
%%sql

DESCRIBE supplier_to_product;

In [ ]:
%%sql

SELECT *
FROM suppliers, supplier_to_product
WHERE suppliers.supplierID = supplier_to_product.supID;

In [ ]:
%%sql

SELECT *
FROM suppliers
INNER JOIN supplier_to_product ON suppliers.supplierID = supplier_to_product.supID;

In [ ]:
%%sql

SELECT *
FROM suppliers
LEFT JOIN supplier_to_product ON suppliers.supplierID = supplier_to_product.supID;

In [ ]:
%%sql

SELECT *
FROM suppliers
RIGHT JOIN supplier_to_product ON suppliers.supplierID = supplier_to_product.supID;

We can concatenate multiple join operations to extract higher level information out of the connections stored in the DB

- Add the corresponding product names the the previous join

In [ ]:
%%sql

DESCRIBE products;

In [ ]:
%%sql

SELECT * FROM products;

In [ ]:
%%sql

DESCRIBE supplier_to_product;

In [ ]:
%%sql

SELECT * FROM supplier_to_product;

In [ ]:
%%sql

SELECT *
FROM supplier_to_product
INNER JOIN suppliers ON suppliers.supplierID = supplier_to_product.supID
INNER JOIN products  ON products.productID   = supplier_to_product.prodID;

The conjunction of `SELECT`, `GROUP BY` and `JOIN` statements will allow us to extract non trivial information out of any Relational DB.

Add the following records to the `supplier_to_product` table and perform the following queries:
    
| supplier | products provided |
| --- | --- | 
| "Wild Hops" | "Founders Porter", "Punk IPA", "HB Dunkel", "Damm Complot" |    
| "Beer Paradise" | "Punk IPA", "Damm Complot" |    
| "Allez Hops! Cave à bièr" | "Founders Porter", "HB Dunkel" |    

1. show all suppliers of "Damm Complot"
2. retrieve the email address of all possible suppliers of "Punk IPA"
3. list the unit price of all products supplied by Italian firms, listed in descending order   

In [ ]:
# import the connector
import mysql.connector

# declare a connection to the MySQL server 
# the hostname (or IP) of the server machine should be passed
db = mysql.connector.connect(
  user="root",
  password="root_pwd",
  host="db", # in this case 'db' is the equivalent of the IP address of the server 
             # or 'localhost' if running mysql locally
)

dbc=db.cursor()

In [ ]:
dbc.execute("USE my_db")

In [ ]:
sql_ = "INSERT INTO supplier_to_product (prodID, supID) VALUES (%s, %s)"
val_ = [
    # supplier Allez Hops
    (1, 2),
    (3, 2),

    # supplier Wild Hops
    (1, 3),
    (2, 3),
    (3, 3),
    (5, 3),

    # supplier Beer Paradise
    (2, 4),
    (5, 4),
]


dbc.executemany(sql_, val_)
db.commit()
     
dbc.execute("SELECT * FROM supplier_to_product"); 
for _ in dbc:
     print(_)

#### 1 - show all suppliers of "Damm Complot"

In [ ]:
%%sql
SELECT *
FROM products;

In [ ]:
%%sql

SELECT suppliers.supplierName
FROM supplier_to_product
INNER JOIN suppliers ON supplier_to_product.supID = suppliers.supplierID
INNER JOIN products ON supplier_to_product.prodID = products.productID
WHERE products.productName = "Damm Complot";

#### 2 - retrieve the email address of all possible suppliers of "Punk IPA"

In [ ]:
%%sql

SELECT suppliers.email 
FROM supplier_to_product
INNER JOIN suppliers ON supplier_to_product.supID = suppliers.supplierID
INNER JOIN products ON supplier_to_product.prodID = products.productID
WHERE products.productName = "Punk IPA";

#### 3 - list the unit price of all products supplied by Italian firms, listed in descending order   

In [ ]:
%%sql

SELECT DISTINCT products.unitPrice, products.productName
FROM supplier_to_product
INNER JOIN suppliers ON supplier_to_product.supID = suppliers.supplierID
INNER JOIN products ON supplier_to_product.prodID = products.productID
WHERE suppliers.countryCode = "ITA"
ORDER BY unitPrice DESC;

## 05 Queries on well-formed DBs

In MySQL we can load entire DBs from external files.

The files will contain the full DB structure (tables and constraints) and will populate all tables with all records 

To load a DB into the MySQL server from the interactive docker shell, we can simply do the following:

1. Create a new DB named `world`
2. Import the content of the file `/mapd-workspace/dbs/world.sql` into the newly created DB via
    
```bash
$ mysql -u root -p world < /mapd-workspace/dbs/world.sql
```

_NB_: The `opt/workspace` directory has been defined as a Docker Volume, and is a shared location with your computer...

In [ ]:
%%sql

CREATE DATABASE IF NOT EXISTS world;

Using the `world` DB, perform queries to answer the folliwing questions.

Additional references can be found here https://dev.mysql.com/doc/world-setup/en/


Use a single query to answer the questions

1. Which country has the largest population?
2. Get the total number of cities in Canada.
3. Select the country with the most cities.
4. List all the languages spoken in the Southeast Asia region.
5. Identify the 5 most spoken language by number of countries.
6. What is the total population of the cities in the Caribbean region?
7. What Countries have a City named "Kingston"?
8. Plot the population density by country, limiting to the 25 with least density.
9. Plot the GNP (Gross Nation Product) of all countries that become independent between 1850 and 1910, limiting to the 10 with highest GNP.
10. Create a scatter plot of the life expentency vs the GNP of all countries that have Spanish as their Official language.


Suggestions:
- Start by inspecting the DB tables structure
- When in doubt, check the table content by selecting a few lines (use `LIMIT` to avoid returining all records)
- Before finalizing the query, you can always perform "intermediate" queries to check if complex operations (groupby and join mostly) are stated correctly

In [ ]:
%%sql

USE world; 

SHOW TABLES;

#### 1 - Which country has the largest population?

In [ ]:
%%sql 
SELECT Name AS Country, Population
FROM country
ORDER BY Population DESC
LIMIT 1;

#### 2 - Get the total number of cities in Canada.

In [ ]:
%%sql

SELECT COUNT(Name) AS numCities
FROM city
WHERE CountryCode IN (SELECT Code FROM country WHERE Name = "Canada");

In [ ]:
%%sql 
#soluzione del prof
SELECT COUNT(Name) AS CitiesInCanada
FROM city
WHERE CountryCode = "CAN";

In [ ]:
%%sql 
SELECT country.Name AS Country, COUNT(city.CountryCode) AS nCity
FROM country
INNER JOIN city ON country.Code = city.CountryCode
WHERE Code = "CAN";

#### 3 - Select the country with the most cities.

In [ ]:
%%sql

SELECT country.Name AS Country, COUNT(city.Name) AS numCity
FROM country,city
WHERE country.Code = city.CountryCode
GROUP BY country.Name
ORDER BY numCity DESC
LIMIT 1;


In [ ]:
%%sql 
#soluzione del prof
SELECT CountryCode, COUNT(1) AS nCities
FROM city
GROUP BY CountryCode
ORDER BY nCities DESC
LIMIT 1;

#### 4 - List all the languages spoken in the 'Southeast Asia' region.

In [ ]:
%%sql

SELECT DISTINCT countrylanguage.Language AS Language
FROM countrylanguage, country
WHERE countrylanguage.CountryCode = country.Code 
AND country.Region = "Southeast Asia";

In [ ]:
%%sql

SELECT Region, COUNT(1) AS nCountry
FROM country 
WHERE Region LIKE "%Asia"
GROUP BY Region;

In [ ]:
%%sql 
SELECT DISTINCT Language
FROM countrylanguage
INNER JOIN country ON countrylanguage.CountryCode = country.Code
WHERE country.Region = 'Southeast Asia'
ORDER BY countrylanguage.Language ASC;

#### 5 - Identify the 5 most spoken language by number of countries.

In [ ]:
%%sql 
SELECT countrylanguage.Language, COUNT(1) AS numCountry
FROM countrylanguage
GROUP BY countrylanguage.Language
ORDER BY numCountry DESC
LIMIT 5;

#### 6 - What is the total population of the cities in the Caribbean region?

In [ ]:
%%sql
SELECT *
FROM city
LIMIT 10;

In [ ]:
%%sql
SELECT SUM(city.Population) AS TotPopulation
FROM city,country
WHERE country.Code = city.CountryCode
AND country.Region  LIKE "Car%";

In [ ]:
%%sql

SELECT SUM(city.Population)
FROM city
LEFT JOIN country ON city.countryCode = country.Code
WHERE country.Region = 'Caribbean';

#soluzione prof

In [ ]:
%%sql
SELECT Region, SUM(city.Population) AS TotalPopulationCity
FROM country
INNER JOIN city ON country.Code = city.CountryCode
WHERE Region ="Caribbean"
GROUP BY Region;

#### 7 - What Countries have a City named "Kingston"?

In [ ]:
%%sql
SELECT country.Name, country.Region
FROM country,city
WHERE country.Code = city.CountryCode
AND city.Name LIKE "Kingston";

In [ ]:
%%sql

SELECT country.Name, country.Region
FROM city
INNER JOIN country on city.CountryCode=country.Code
WHERE city.Name ="Kingston";

#### 8 - Plot the population density by country, limiting to the 25 with least density.

In [ ]:
df_density =%sql SELECT country.Name,country.Population/country.SurfaceArea AS PopDensity FROM country ORDER BY PopDensity LIMIT 25;
df_density_pd = pd.DataFrame(df_density)

fig,ax =plt.subplots(1,1,figsize=(18,9))

ax.bar(df_density_pd["Name"],df_density_pd["PopDensity"])
ax.tick_params(axis='x', rotation=90)
plt.show()

In [ ]:
res_ = %sql SELECT  Name, Population/SurfaceArea AS density FROM  country  ORDER BY density ASC  LIMIT 25;

print(res_)

plt.figure(figsize=(16,3))
res_.bar();
plt.xticks(rotation='vertical');

#### 9 - Plot the GNP (Gross Nation Product) of all countries that become independent between 1850 and 1910, limiting to the 10 with highest GNP.

In [ ]:
Gnp=%sql\
SELECT Name,GNP\
FROM country\
WHERE IndepYear BETWEEN 1850 AND 1910\
ORDER BY GNP DESC\
LIMIT 10;

df_gnp=pd.DataFrame(Gnp)

fig,ax =plt.subplots(1,1,figsize=(18,9))

ax.bar(df_gnp["Name"],df_gnp["GNP"])
ax.tick_params(axis='x', rotation=90)
plt.show()

In [ ]:
res_ = %sql SELECT  Name, GNP   FROM  country  WHERE  (IndepYear > 1850 AND IndepYear < 1910)  ORDER BY GNP DESC LIMIT 10;

print(res_)

plt.figure(figsize=(16,3))
res_.bar();
plt.xticks(rotation='vertical');

#### 10 - Create a scatter plot of the life expentency vs the GNP of all countries that have Spanish as their Official language.

In [ ]:
df_gnp_sp_pandas

In [ ]:
df_gnp_sp=%sql\
SELECT country.Name,country.GNP,country.LifeExpectancy\
FROM country,countrylanguage\
WHERE country.Code = countrylanguage.CountryCode\
AND Language LIKE "Sp%"\
AND isOfficial = "T"\
ORDER BY country.GNP;

df_gnp_sp_pandas=pd.DataFrame(df_gnp_sp)

fig,ax =plt.subplots(1,1,figsize=(18,9))

ax.scatter(df_gnp_sp_pandas["GNP"],df_gnp_sp_pandas["LifeExpectancy"])

for i in range(len(df_gnp_sp_pandas)):
    country_name = df_gnp_sp_pandas.iloc[i]["Name"]
    x = df_gnp_sp_pandas.iloc[i]["GNP"]
    y = df_gnp_sp_pandas.iloc[i]["LifeExpectancy"]
    ax.annotate(country_name, (x, y), textcoords="offset points", xytext=(0,10), ha='center')

plt.show()

In [ ]:
res_ = %sql SELECT  LifeExpectancy, GNP, country.Name \
            FROM  country\
            RIGHT JOIN  countrylanguage ON  country.Code = countrylanguage.CountryCode \
            WHERE countrylanguage.Language = "Spanish"\
            AND IsOfficial = 1;

print(res_)

plt.figure(figsize=(8,6))
for _ in res_:
    plt.scatter(_[0],_[1],s=50);
    plt.annotate(_[2], (float(_[0])*1.002,float(_[1])*1.002));
plt.ylabel('GNP')
plt.xlabel('LifeExpectancy')
plt.yscale('log')

## 06 More on queries 

Let' import a well-structured DB, with several tables and relationships, to be used as a sandbox for further exercises on queries.

The `.sql` file can be found at: `/mapd-workspace/dbs/IMDb_pruned.sql`.

The DB is freely available and is taken from the IMDb (Internet Movie Database) website (https://www.imdb.com/interfaces/).

The entire database is composed of a dozen of tables, hosing all people involved in Movies, Shorts, TV Show Epidoses and more since the 1890s. 

To simplify the execution of queries, we will work with a slimmed-down version of the entire DB, with still plenty of records for us to extract interesting information.

1. Create a new DB named `IMDb`
2. Import the content of the file `/mapd-workspace/dbs/IMDb_pruned.sql` into the newly created DB
(this might take a minute or two...)

In [ ]:
%%sql
CREATE DATABASE IF NOT EXISTS IMDb;

### Check which tables are available

In [ ]:
%%sql

USE IMDb;
SHOW TABLES;

### Describe the content of table Names_

In [ ]:
%%sql

DESCRIBE Names_;

### People by birth year

A) Start by limiting the query to 1000 entries

1. Draw an histogram of the year of birth
2. Draw a second histogram with the year of birth of the 1000 youngest people in the list

In [ ]:
births=%sql\
SELECT birth_year\
FROM Names_\
LIMIT 1000;

births_np=np.array(births)
plt.hist(births_np)
plt.show()

In [ ]:
import mysql.connector
import itertools
import matplotlib.pyplot as plt

In [ ]:
#A.1
db = mysql.connector.connect(
  user="root",
  password="root_pwd",
  host="db"
)

dbc = db.cursor()

dbc.execute("USE IMDb")

dbc.execute("SELECT birth_year FROM Names_ LIMIT 1000")
birth_year = dbc.fetchall() 

In [ ]:
fig,ax=plt.subplots(1,1, figsize=(8,8))
ax.hist([x[0] for x in birth_year])
plt.show()

In [ ]:
# A.2
dbc.execute("SELECT birth_year FROM Names_ ORDER BY birth_year DESC LIMIT 1000")
birth_year_young = dbc.fetchall() 

fig,ax=plt.subplots(1,1, figsize=(8,8))
ax.hist([x[0] for x in birth_year_young])
plt.show()

B) Extend the query to all records in the table

1. Check for outliers (inspect min and max)
2. If any outlier is found, limit the query to a reasonable range (at least people born after 1850)
3. Draw a new histogram with the year of birth
4. Compute the mean and std of year of birth

In [ ]:
%%sql
SELECT *
FROM Names_
WHERE (birth_year < 1850 OR birth_year > 2023);

In [ ]:
births2=%sql\
SELECT birth_year\
FROM Names_\
WHERE birth_year > 1850;

plt.hist(np.array(births2),bins=50)
plt.axvline(np.mean(np.array(births2)),linestyle="dashed",color="black")

summary_text="Mean: {}\nStd:{}".format(np.round(np.mean(np.array(births2)),3),np.round(np.std(np.array(births2)),3))
plt.text(0.05, 0.9, summary_text, transform=plt.gca().transAxes, ha='left', va='top')
plt.show()

In [ ]:
%%sql
SELECT ROUND(AVG(birth_year),3) AS Mean,ROUND(STD(birth_year),3) AS Std
FROM Names_
WHERE birth_year > 1850

In [ ]:
%%sql
#B.1
USE IMDb;

SELECT MIN(birth_year) AS Min ,MAX(birth_year) AS Max 
FROM Names_;

In [ ]:
%%sql
#B.2
SELECT birth_year,name_
FROM Names_ 
WHERE (birth_year < 1850);

In [ ]:
# Karen Abercrombie - 1964
#Sophie Oliver - 1988

In [ ]:
# B.3
dbc.execute("SELECT birth_year FROM Names_ WHERE birth_year > 1850")
birth_year_all = dbc.fetchall() 

fig,ax=plt.subplots(1,1, figsize=(8,8))
ax.hist([x[0] for x in birth_year_all],bins=50)
plt.show()

In [ ]:
# B.4
dbc.execute("SELECT AVG(birth_year) AS mean, STD(birth_year) AS std FROM Names_ WHERE (birth_year > 1850)")
birth_stats = dbc.fetchall()

In [ ]:
birth_stats

### Movie stats

1. Plot how many titles can be found in the DB per year, over the past 25 years
2. List the names of all actors who have had the role of Spider-Man and the corresponding Title
3. List and count the 10 people who appeared the most in movies by "Wes Anderson"

In [ ]:
%%sql
SHOW TABLES;

In [ ]:
%%sql
DESCRIBE Had_role;

In [ ]:
%%sql
DESCRIBE Titles;

In [ ]:
%%sql
DESCRIBE Names_;

In [ ]:
%%sql
DESCRIBE Directors;

In [ ]:
%%sql
DESCRIBE Title_ratings;

#### 1 - Plot how many titles can be found in the DB per year, over the past 25 years

In [ ]:
movies=%sql\
SELECT start_year,COUNT(primary_title) AS numMovie\
FROM Titles\
WHERE title_type = "movie"\
AND start_year < 2023\
GROUP BY start_year\
ORDER BY start_year DESC\
LIMIT 25;

movies_df=pd.DataFrame(movies)
plt.plot(movies_df["start_year"],movies_df["numMovie"])
plt.show()

In [ ]:
dbc.execute("SELECT start_year, COUNT(1) FROM Titles WHERE start_year < 2023 AND title_type = 'movie' GROUP BY start_year ORDER BY start_year DESC LIMIT 25")
film_year=dbc.fetchall()

In [ ]:
fig,ax=plt.subplots(1,1,figsize=(8,8))

ax.plot([x[0] for x in film_year], [x[1] for x in film_year])

plt.show()

#### 2 - List the names of all actors who have had the role of Spider-Man and the corresponding Title 

In [ ]:
%%sql
SELECT Names_.name_ AS Actor, Titles.primary_title AS Title
FROM Names_,Titles, Had_role
WHERE Names_.name_id = Had_role.name_id
AND Titles.title_id = Had_role.title_id
AND Had_role.role_ LIKE "Spider%an%"
ORDER BY Actor
LIMIT 10;

In [ ]:
%%sql
SELECT DISTINCT Names_.name_ AS Name, Titles.primary_title AS Title
FROM Had_role
INNER JOIN Names_ ON Names_.name_id = Had_role.name_id
INNER JOIN Titles ON Titles.title_id = Had_role.title_id
WHERE role_ LIKE "Spider-Man";

#### 3 - List and count the 10 people who appeared the most in movies by "Wes Anderson"

In [ ]:
%%sql

DESCRIBE Directors;

In [ ]:
%%sql

SELECT Directors.title_id
FROM Directors
INNER JOIN Names_ ON Directors.name_id = Names_.name_id
WHERE Names_.name_ = "Wes Anderson";

In [ ]:
%%sql 

SELECT Names_.name_ AS Name, COUNT(1) AS Appereance
FROM Had_role
INNER JOIN Names_ ON Had_role.name_id = Names_.name_id
WHERE (Had_role.title_id IN (
    SELECT Directors.title_id 
    FROM Directors
    INNER JOIN Names_ ON Directors.name_id = Names_.name_id
    WHERE (Names_.name_ LIKE "Wes Anderson" )
    ))
GROUP BY Names_.name_
ORDER BY Appereance DESC
LIMIT 10;

### Is the IMDB only about movies? 

1. Check the number of different media types contained in the DB
2. Plot an histogram about the number of media types per group
3. Find the name and rating of the oldest videogame stored in the DB 

#### 1 - Check the number of different media types contained in the DB

In [ ]:
%%sql

SELECT DISTINCT title_type AS MediaType, COUNT(1) AS NumberOf
FROM Titles
GROUP BY title_type;

#### 2 - Plot an histogram about the number of media types per group

In [ ]:
dbc.execute("SELECT title_type FROM Titles")
result = dbc.fetchall() 

fig,ax=plt.subplots(1,1, figsize=(8,8))
ax.hist([x[0] for x in result])
plt.show()

#### 3 - Find the name and rating of the oldest videogame stored in the DB 

In [ ]:
%%sql
DESCRIBE Title_ratings;

In [ ]:
%%sql
DESCRIBE Titles;

In [ ]:
%%sql
SELECT MIN(Titles.start_year)
FROM Titles
WHERE (Titles.title_type = 'videoGame')
LIMIT 10;

In [ ]:
%%sql
SELECT Titles.primary_title AS Title ,Title_ratings.average_rating AS Rating
FROM Titles
INNER JOIN Title_ratings ON Title_ratings.title_id = Titles.title_id
WHERE (Titles.title_type = "videoGame")
ORDER BY Titles.start_year ASC
LIMIT 10;

In [ ]:
%%sql
SELECT Titles.start_year AS Year,Titles.primary_title AS Name, Title_ratings.average_rating AS Rating
FROM Titles,Title_ratings
WHERE Titles.title_id = Title_ratings.title_id
AND Titles.title_type LIKE "vide%"
ORDER BY Year
LIMIT 1;

### Identify interesting outliers 

1. List the names of movies whose title begin with "The" have a runtime between 3 and 4 hours.
2. What actor had the most roles as 'Self'?
3. Identify what TV series had more than 1,000 episodes, and check the first- and last-episod year

#### 1 - List the names of movies whose title begin with "The" have a runtime between 3 and 4 hours.

In [ ]:
%%sql
SELECT Titles.primary_title AS Title
FROM Titles
WHERE (Titles.primary_title LIKE "The%" 
       AND (Titles.runtime_minutes BETWEEN (3*60) AND (4*60)) 
       AND Titles.title_type = "movie");

In [ ]:
%%sql
DESCRIBE Names_;

#### 2 - What actor had the most roles as 'Self'?

In [ ]:
%%sql 

SELECT Names_.name_ AS Actor, COUNT(1) AS Times
FROM Names_
INNER JOIN Had_role ON Names_.name_id = Had_role.name_id
WHERE Had_role.role_ = "Self"
GROUP BY Names_.name_
ORDER BY Times DESC
LIMIT 10;

#### 3 - Identify what TV series had more than 1,000 episodes, and check the first- and last-episod year

In [ ]:
%%sql
SHOW TABLES;

In [ ]:
%%sql 

SELECT DISTINCT title_type
FROM Titles;

In [ ]:
%%sql 

SELECT *
FROM Titles
LIMIT 10;

In [ ]:
%%sql

CREATE VIEW Tv1KEpisodes AS
SELECT Titles.primary_title, Titles.title_id,Titles.start_year, COUNT(1)
FROM Episode_belongs_to
INNER JOIN Titles ON Titles.title_id = Episode_belongs_to.parent_tv_show_title_id
WHERE Titles.title_type IN ("tvEpisode","tvSeries","tvMiniSeries")
GROUP BY Titles.primary_title,Titles.title_id,Titles.start_year
HAVING COUNT(1)>1000
ORDER BY COUNT(1) DESC;

In [ ]:
%%sql
SELECT *
FROM Tv1KEpisodes
LIMIT 10;

### It's all about the ratings 

1. Group all movies by decade and plot the rating distribution. Limit the query to the movies with at least 1000 ratings.
2. Plot the average rating of each episode of Games of Thrones. Group by season and compute the average and std for each season
3. Plot the total numer of movies per year, divided by genre (Action, Comedy, Drama, Thriller, Fantasy), and the yearly rating average per genre

In [4]:
%%sql
SHOW TABLES;

 * mysql+mysqlconnector://root:***@db
7 rows affected.


[('Directors',),
 ('Episode_belongs_to',),
 ('Had_role',),
 ('Names_',),
 ('Title_genres',),
 ('Title_ratings',),
 ('Titles',)]

In [6]:
%%sql
DESCRIBE Titles;

 * mysql+mysqlconnector://root:***@db
5 rows affected.


[('title_id', b'varchar(255)', 'NO', '', None, ''),
 ('title_type', b'varchar(50)', 'YES', '', None, ''),
 ('primary_title', b'text', 'YES', '', None, ''),
 ('start_year', b'int', 'YES', '', None, ''),
 ('runtime_minutes', b'int', 'YES', '', None, '')]

In [17]:
%%sql
SELECT FLOOR(Titles.start_year/10)*10 AS Year,ROUND(AVG(Title_ratings.average_rating),3) AS Rating
FROM Title_ratings,Titles
WHERE Titles.title_id = Title_ratings.title_id
AND Title_ratings.num_votes > 1000
AND Titles.title_type LIKE "mov%"
AND Titles.start_year >0
GROUP BY Year
ORDER BY Year;

 * mysql+mysqlconnector://root:***@db
4 rows affected.


[(1990, 6.365), (2000, 6.246), (2010, 6.158), (2020, 6.269)]

In [34]:
%%sql
SELECT *
FROM Titles
WHERE primary_title LIKE "Game%"
AND title_type = "tvSeries";

 * mysql+mysqlconnector://root:***@db
67 rows affected.


[('tt0111976', 'tvSeries', b'Game-On', 1995, 29),
 ('tt0200339', 'tvSeries', b'Gamesmaster', 1992, 30),
 ('tt0222562', 'tvSeries', b'Games World', 1993, 30),
 ('tt0329834', 'tvSeries', b'Game k n b?', 2001, 30),
 ('tt0397149', 'tvSeries', b'Game Over', 2004, 30),
 ('tt0415425', 'tvSeries', b'GamePro TV', 1991, 30),
 ('tt0481433', 'tvSeries', b'Gameshow Marathon', 2005, 60),
 ('tt0787359', 'tvSeries', b'Gameshow Marathon', 2006, 60),
 ('tt0944947', 'tvSeries', b'Game of Thrones', 2011, 57),
 ('tt0978760', 'tvSeries', b'Game Show in My Head', 2009, 30),
 ('tt10047072', 'tvSeries', b'Game of Vengeance', 2017, 60),
 ('tt10660928', 'tvSeries', b'Game Development Girls', 2016, 7),
 ('tt11182506', 'tvSeries', b'Game on', 2019, 15),
 ('tt1126141', 'tvSeries', b'Game Ranger Diaries', 2006, 45),
 ('tt1169475', 'tvSeries', b'Game One', 2006, 15),
 ('tt1181053', 'tvSeries', b'GameTrailers TV with Geoff Keighley', 2008, 21),
 ('tt12033954', 'tvSeries', b'GameBoy', 2018, 15),
 ('tt1217344', 'tvSeries', b'Gamekings', 2002, 60),
 ('tt12398184', 'tvSeries', b'Games People Play', 2020, 25),
 ('tt12788738', 'tvSeries', b'Gameplay', 2019, 31),
 ('tt12800428', 'tvSeries', b'Game On! A Comedy Crossover Event', 2020, 30),
 ('tt1280873', 'tvSeries', b"Gamecaster's Battlefield 2142 Invitational", 2007, 27),
 ('tt13650788', 'tvSeries', b'Gamer Sapiens', 2020, 43),
 ('tt13787426', 'tvSeries', b'Game the Gamer', 2017, 28),
 ('tt14456558', 'tvSeries', b'Game of Games - Gioco Loco', 2021, 120),
 ('tt15113726', 'tvSeries', b'Game Making of ABE CHUP', 2021, 49),
 ('tt15422806', 'tvSeries', b'Game of Chefs', 2021, 55),
 ('tt1621440', 'tvSeries', b'Game Chasers', 2010, 30),
 ('tt16266484', 'tvSeries', b'Game of Games Suomi', 2021, 90),
 ('tt18069546', 'tvSeries', b'Game Master', 2020, 16),
 ('tt1893804', 'tvSeries', b'Game On! With John Salley', 2011, 30),
 ('tt1954469', 'tvSeries', b'Gamer Chick', 2011, 49),
 ('tt2275071', 'tvSeries', b'Game of Silence', 2012, 90),
 ('tt2371737', 'tvSeries', b'Games World', 1994, 45),
 ('tt2385523', 'tvSeries', b'Game Plan', 2012, 10),
 ('tt2389040', 'tvSeries', b'Game Knights', 2012, 15),
 ('tt2660690', 'tvSeries', b'Game Bang', 2012, 15),
 ('tt2713808', 'tvSeries', b'Game Stain', 2012, 2),
 ('tt2913444', 'tvSeries', b'Game Over', 2012, 6),
 ('tt2916224', 'tvSeries', b'GameTime PlayTime', 2013, 6),
 ('tt3214726', 'tvSeries', b'Game Changers', 2013, 30),
 ('tt3402704', 'tvSeries', b'Game of the Week', 2013, 180),
 ('tt3407936', 'tvSeries', b'Game Frame', 2013, 10),
 ('tt3473774', 'tvSeries', b'Game of Pawns', 2013, 30),
 ('tt3779600', 'tvSeries', b'Game Night', 2014, 22),
 ('tt4074374', 'tvSeries', b'Game of Silence', 2016, 60),
 ('tt4299962', 'tvSeries', b'GameStop Trolled', 2013, 8),
 ('tt4326802', 'tvSeries', b'Games Magazine', 2007, 30),
 ('tt4351710', 'tvSeries', b'Game On', 2015, 30),
 ('tt4380272', 'tvSeries', b"Gamer's Guide to Pretty Much Everything", 2015, 22),
 ('tt4532812', 'tvSeries', b'Games of Strange', 2015, 26),
 ('tt4711184', 'tvSeries', b'Game Shakers', 2015, 30),
 ('tt4896860', 'tvSeries', b'Game Trails', 2004, 30),
 ('tt4967358', 'tvSeries', b'GameStar: Die Redaktion', 2004, 20),
 ('tt5128580', 'tvSeries', b'Games from the Chippy', 2012, 15),
 ('tt6026194', 'tvSeries', b'Game Winning Hit', 2009, 90),
 ('tt6259652', 'tvSeries', b'Game Two', 2016, 45),
 ('tt6620620', 'tvSeries', b'GameFace', 2017, 24),
 ('tt6819260', 'tvSeries', b'Gamebros', 2018, 45),
 ('tt7095890', 'tvSeries', b'Gameballcz', 2012, 10),
 ('tt7163698', 'tvSeries', b'Gamers!', 2017, 24),
 ('tt7174180', 'tvSeries', b'Game Changers', 2015, 22),
 ('tt7292160', 'tvSeries', b'Game', 2016, 60),
 ('tt8227510', 'tvSeries', b'Gameday Commute', 2017, 13),
 ('tt8319644', 'tvSeries', b'Games People Play', 2019, 60),
 ('tt8559270', 'tvSeries', b"Gamer's Paradise", 2019, 30),
 ('tt9810460', 'tvSeries', b'Games Night', 2015, 23)]

In [37]:
%%sql
SELECT Episode_belongs_to.season_number, Episode_belongs_to.episode_number,Title_ratings.average_rating
FROM Episode_belongs_to,Title_ratings
WHERE Episode_belongs_to.episode_title_id = Title_ratings.title_id
AND parent_tv_show_title_id IN (SELECT Titles.title_id 
                                FROM Titles
                                WHERE primary_title = "Game of Thrones")
ORDER BY season_number,episode_number
LIMIT 10;

 * mysql+mysqlconnector://root:***@db
10 rows affected.


[(1, 1, 9.1),
 (1, 2, 8.8),
 (1, 3, 8.7),
 (1, 4, 8.8),
 (1, 5, 9.1),
 (1, 6, 9.2),
 (1, 7, 9.2),
 (1, 8, 9.0),
 (1, 9, 9.6),
 (1, 10, 9.5)]

In [38]:
import pandas as pd
import matplotlib.pyplot as plt

In [44]:
ratings=%sql\
SELECT Episode_belongs_to.season_number, Episode_belongs_to.episode_number,Title_ratings.average_rating\
FROM Episode_belongs_to,Title_ratings\
WHERE Episode_belongs_to.episode_title_id = Title_ratings.title_id\
AND parent_tv_show_title_id IN (SELECT Titles.title_id \
                                FROM Titles\
                                WHERE primary_title = "Game of Thrones")\
ORDER BY season_number,episode_number;

ratings_pd = pd.DataFrame(ratings)
ratings_pd["index"] = ratings_pd.index+1

 * mysql+mysqlconnector://root:***@db
73 rows affected.


#### 1 - Group all movies by decade and plot the rating distribution. Limit the query to the movies with at least 1000 ratings.

In [18]:
%%sql

SELECT Titles.primary_title, 10*FLOOR(Titles.start_year/10) AS Decade, Title_ratings.average_rating, Title_ratings.num_votes
FROM Title_ratings
INNER JOIN Titles ON Titles.title_id = Title_ratings.title_id
WHERE (Title_ratings.num_votes>1000 AND Titles.title_type = "movie" AND Titles.start_year IS NOT NULL)
ORDER BY Titles.start_year ASC;

 * mysql+mysqlconnector://root:***@db
26827 rows affected.


[(b'Abuk Sabuk 1 Film', 1990, 6.3, 1107),
 (b'Gremlins 2: The New Batch', 1990, 6.4, 100985),
 (b'A Nymphoid Barbarian in Dinosaur Hell', 1990, 2.7, 1678),
 (b'Come See the Paradise', 1990, 6.7, 2792),
 (b'Edward Scissorhands', 1990, 7.9, 472358),
 (b'Shadowzone', 1990, 5.1, 1096),
 (b'No: 20 Madras Mail', 1990, 7.7, 1187),
 (b'Narrow Margin', 1990, 6.6, 8956),
 (b'White Palace', 1990, 6.5, 8084),
 (b'The Prisoner', 1990, 5.8, 3529),
 (b'My Blue Heaven', 1990, 6.3, 20416),
 (b'RoboCop 2', 1990, 5.8, 85098),
 (b'American Ninja 4: The Annihilation', 1990, 4.0, 4921),
 (b"Child's Play 2", 1990, 5.9, 49928),
 (b'The Russia House', 1990, 6.1, 15887),
 (b'Maniac Nurses find Ecstasy', 1990, 2.8, 1185),
 (b'The Freshman', 1990, 6.5, 19873),
 (b'The Witches', 1990, 6.9, 48558),
 (b'City Life', 1990, 7.9, 4109),
 (b'Faces of Death IV', 1990, 3.4, 1217),
 (b'Swarg', 1990, 6.7, 1415),
 (b'Rosencrantz & Guildenstern Are Dead', 1990, 7.4, 21788),
 (b'Young Guns II', 1990, 6.5, 35204),
 (b'Def by Temptation', 1990, 4.9, 1578),
 (b"Macken - Roy's & Roger's Bilservice", 1990, 6.1, 1097),
 (b'Koko Flanel', 1990, 6.3, 2194),
 (b'Bullet in the Head', 1990, 7.6, 10570),
 (b'A Shock to the System', 1990, 6.7, 4891),
 (b'Solar Crisis', 1990, 4.0, 1904),
 (b'The Two Jakes', 1990, 6.2, 13760),
 (b'Frankenstein Unbound', 1990, 5.5, 3774),
 (b'Pacific Heights', 1990, 6.4, 19916),
 (b'Awakenings', 1990, 7.8, 136225),
 (b'Sgt. Kabukiman N.Y.P.D.', 1990, 5.8, 2939),
 (b'Coupe de Ville', 1990, 6.7, 2468),
 (b'Far Out Man', 1990, 5.0, 1113),
 (b'Home Alone', 1990, 7.6, 547692),
 (b'Auntie Danielle', 1990, 7.1, 3500),
 (b'Die Hard 2', 1990, 7.1, 354604),
 (b'The Invisible Maniac', 1990, 4.0, 2725),
 (b'Bird on a Wire', 1990, 6.0, 43697),
 (b'Brain Dead', 1990, 6.0, 4511),
 (b'Soultaker', 1990, 2.4, 3833),
 (b"S'en fout la mort", 1990, 6.7, 1059),
 (b'Back to the Future Part III', 1990, 7.4, 430815),
 (b'The Ages of Lulu', 1990, 5.6, 3789),
 (b'Fantozzi alla riscossa', 1990, 5.8, 1447),
 (b'Love at Large', 1990, 5.7, 1275),
 (b"Miller's Crossing", 1990, 7.7, 132827),
 (b'Predator 2', 1990, 6.3, 156925),
 (b'Trust', 1990, 7.4, 11146),
 (b'The Crawlers', 1990, 2.8, 1358),
 (b'First Rank', 1990, 5.3, 1146),
 (b'Hamlet', 1990, 6.7, 22233),
 (b'Henry & June', 1990, 6.3, 13091),
 (b'Slacker', 1990, 7.1, 21192),
 (b'Werner - Beinhart!', 1990, 6.7, 5708),
 (b'Halfaouine: Boy of the Terraces', 1990, 6.7, 1303),
 (b'Demonia', 1990, 4.6, 1506),
 (b'Alienator', 1990, 3.2, 1599),
 (b'Baby Blood', 1990, 6.0, 1838),
 (b'Catchfire', 1990, 5.3, 3916),
 (b'A Tale of Springtime', 1990, 7.2, 4429),
 (b'Dezha vyu', 1990, 7.6, 1356),
 (b'Flesh Gordon Meets the Cosmic Cheerleaders', 1990, 3.7, 1590),
 (b'I Bought a Vampire Motorcycle', 1990, 5.6, 1237),
 (b'In the Cold of the Night', 1990, 4.4, 1621),
 (b'The Local Stigmatic', 1990, 5.8, 1561),
 (b'Mathilukal', 1990, 8.4, 1245),
 (b'May Fools', 1990, 7.3, 3124),
 (b'Moon 44', 1990, 5.1, 5168),
 (b'Prom Night III: The Last Kiss', 1990, 4.6, 2194),
 (b'Spontaneous Combustion', 1990, 4.8, 2593),
 (b'The Death King', 1990, 6.5, 2502),
 (b'The Match Factory Girl', 1990, 7.6, 9723),
 (b'The Voice of the Moon', 1990, 6.3, 2908),
 (b'Three Men and a Little Lady', 1990, 5.5, 24352),
 (b'Boiling Point', 1990, 6.8, 6699),
 (b'The Adventures of Ford Fairlane', 1990, 6.4, 17944),
 (b'After Dark, My Sweet', 1990, 6.6, 3535),
 (b'Agneepath', 1990, 7.7, 8842),
 (b'Air America', 1990, 5.8, 28370),
 (b'Alice', 1990, 6.6, 14174),
 (b'Almost an Angel', 1990, 5.6, 4552),
 (b'The Ambulance', 1990, 5.9, 3512),
 (b'An Angel at My Table', 1990, 7.5, 7585),
 (b'Anjali', 1990, 8.2, 2951),
 (b'Another 48 Hrs.', 1990, 5.9, 40967),
 (b'Arachnophobia', 1990, 6.4, 68381),
 (b'Archangel', 1990, 6.5, 1440),
 (b'Avalon', 1990, 7.2, 6238),
 (b'BlackJack', 1990, 5.7, 1531),
 (b'Miami Blues', 1990, 6.4, 8549),
 (b'Across the Tracks', 1990, 5.8, 2395),
 (b'Death in Brunswick', 1990, 6.6, 1211),
 (b'Boynu B\xc3\xbck\xc3\xbck K\xc3\xbcheylan', 1990, 6.4, 1063),
 (b'House P

In [19]:
%%sql

SELECT 10*FLOOR(Titles.start_year/10) AS Decade, AVG(Title_ratings.average_rating) AS MeanRating
FROM Title_ratings
INNER JOIN Titles ON Titles.title_id = Title_ratings.title_id
WHERE (Title_ratings.num_votes>1000 AND Titles.title_type = "movie" AND Titles.start_year IS NOT NULL)
GROUP BY Decade
ORDER BY Decade ASC;

 * mysql+mysqlconnector://root:***@db
4 rows affected.


[(1990, 6.364565547778342),
 (2000, 6.246381951759197),
 (2010, 6.158357727336619),
 (2020, 6.268965520191386)]

In [ ]:
dbc.execute("SELECT 10*FLOOR(Titles.start_year/10) AS Decade, AVG(Title_ratings.average_rating) AS MeanRating FROM Title_ratings INNER JOIN Titles ON Titles.title_id = Title_ratings.title_id WHERE (Title_ratings.num_votes>1000 AND Titles.title_type = 'movie' AND Titles.start_year IS NOT NULL) GROUP BY Decade ORDER BY Decade ASC")

result = dbc.fetchall() 

fig,ax=plt.subplots(1,1, figsize=(8,8))
ax.scatter([x[0] for x in result],[x[1] for x in result])
ax.plot([x[0] for x in result],[x[1] for x in result],linestyle="dashed")
plt.show()

#### 2 - Plot the average rating of each episode of Games of Thrones. Group by season and compute the average and std for each season

In [ ]:
%%sql
DESCRIBE Episode_belongs_to;

In [ ]:
%%sql
SELECT Episode_belongs_to.season_number AS Season,Episode_belongs_to.episode_number AS Episode, Title_ratings.average_rating AS Rating
FROM Episode_belongs_to
INNER JOIN Title_ratings ON Episode_belongs_to.episode_title_id = Title_ratings.title_id
LIMIT 10;

In [ ]:
%%sql

SELECT T.primary_title, E.season_number, E.episode_number, R.average_rating
FROM Episode_belongs_to E
INNER JOIN Titles T ON T.title_id = E.episode_title_id
INNER JOIN Title_ratings R ON R.title_id = E.episode_title_id
WHERE parent_tv_show_title_id = (
    SELECT title_id
    FROM Titles
    WHERE primary_title = 'Game of Thrones'
    AND title_type = 'tvSeries'
)
ORDER BY E.season_number;

In [ ]:
%%sql

SELECT E.season_number, AVG(R.average_rating), STD(R.average_rating)
FROM Episode_belongs_to E
INNER JOIN Titles T ON T.title_id = E.episode_title_id
INNER JOIN Title_ratings R ON R.title_id = E.episode_title_id
WHERE parent_tv_show_title_id = (
    SELECT title_id
    FROM Titles
    WHERE primary_title = 'Game of Thrones'
    AND title_type = 'tvSeries'
)
GROUP BY E.season_number
ORDER BY E.season_number;

In [ ]:
sql_="SELECT E.season_number, AVG(R.average_rating), STD(R.average_rating) \
FROM Episode_belongs_to E \
INNER JOIN Titles T ON T.title_id = E.episode_title_id \
INNER JOIN Title_ratings R ON R.title_id = E.episode_title_id \
WHERE parent_tv_show_title_id = ( \
    SELECT title_id \
    FROM Titles \
    WHERE primary_title = 'Game of Thrones' \
    AND title_type = 'tvSeries' \
) \
GROUP BY E.season_number \
ORDER BY E.season_number"

dbc.execute(sql_)
result=dbc.fetchall()

fig,ax=plt.subplots(1,1, figsize=(8,8))
ax.scatter([x[0] for x in result],[x[1] for x in result])
ax.plot([x[0] for x in result],[x[1] for x in result],linestyle="dashed")
ax.errorbar([x[0] for x in result],[x[1] for x in result],
            yerr=[x[2] for x in result], xerr=None,
            linestyle="none",capsize=3)
plt.show()

#### 3 - Plot the total numer of movies per year, divided by genre (Action, Comedy, Drama, Thriller, Fantasy), and the yearly rating average per genre

In [ ]:
%%sql
SHOW TABLES;

In [ ]:
%%sql
DESCRIBE Title_genres;

In [ ]:
%%sql
DESCRIBE Title_ratings;

In [ ]:
%%sql
SELECT Titles.start_year, Title_genres.genre, COUNT(2) AS nMovies, AVG(Title_ratings.average_rating) AS Rating
FROM Titles
INNER JOIN Title_genres ON Titles.title_id = Title_genres.title_id
INNER JOIN Title_ratings ON Titles.title_id = Title_ratings.title_id
WHERE (Titles.title_type = 'movie' AND Titles.start_year IS NOT NULL)
GROUP BY Titles.start_year, Title_genres.genre
ORDER BY Titles.start_year;

In [ ]:
dbc.execute("SELECT Titles.start_year, Title_genres.genre, COUNT(2) AS nMovies, AVG(Title_ratings.average_rating) AS Rating \
FROM Titles \
INNER JOIN Title_genres ON Titles.title_id = Title_genres.title_id \
INNER JOIN Title_ratings ON Titles.title_id = Title_ratings.title_id \
WHERE (Titles.title_type = 'movie' AND Titles.start_year IS NOT NULL AND Title_genres.genre IN ('Action', 'Comedy', 'Drama', 'Thriller', 'Fantasy')) \
GROUP BY Titles.start_year, Title_genres.genre \
ORDER BY Titles.start_year")

result=dbc.fetchall()

df = pd.DataFrame(result, columns=['start_year', 'genre', 'nMovies','Rating'])

In [ ]:
fig,ax=plt.subplots(1,1,figsize=(10,8))

for i in df.genre.unique():
    ax.plot(df[df.genre == i].start_year,df[df.genre == i].nMovies,label=i)
    
ax.legend()
plt.show()

In [ ]:
fig,ax=plt.subplots(1,1,figsize=(10,8))

for i in df.genre.unique():
    ax.plot(df[df.genre == i].start_year,df[df.genre == i].Rating,label=i)
    
ax.legend()
plt.show()